In [5]:
import pandas as pd
import os
import re
import plotly.express as px

# Unir CSVs

## Air Quality

In [6]:
# Ruta de la carpeta donde están los CSV
carpeta_resultados = r"C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\resultados"

# Listar todos los archivos que terminan en .csv
archivos_csv = [archivo for archivo in os.listdir(carpeta_resultados) if archivo.endswith('.csv')]

# Leer y unir todos los archivos
dfs = []
for archivo in archivos_csv:
    ruta = os.path.join(carpeta_resultados, archivo)
    try:
        df = pd.read_csv(ruta, encoding='utf-8-sig')
        df['archivo_origen'] = archivo  # Guarda el nombre del archivo

        # Extraer ID y año del nombre del archivo, e.g., 123456_2024_aire.csv
        match = re.match(r"(\d+)_([0-9]{4})_aire\.csv", archivo)
        if match:
            df['ciudad_id'] = match.group(1)
            df['anio'] = match.group(2)
        else:
            df['ciudad_id'] = None
            df['anio'] = None

        dfs.append(df)
    except Exception as e:
        print(f"❌ Error al leer {archivo}: {e}")

# Unir todos los dataframes
df_unido = pd.concat(dfs, ignore_index=True)

# ❗ Filtrar solo los archivos del año 2024
df_unido = df_unido[df_unido['anio'] == '2024']

# Guardar el archivo final
ruta_salida = os.path.join(carpeta_resultados, "calidad_aire_2024.csv")
df_unido.to_csv(ruta_salida, index=False, encoding='utf-8-sig')

print(f"✅ Archivo combinado guardado en: {ruta_salida}")


✅ Archivo combinado guardado en: C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\resultados\calidad_aire_2024.csv


In [7]:
df_unido.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1872822 entries, 365 to 2418496
Data columns (total 11 columns):
 #   Column            Dtype  
---  ------            -----  
 0   date              object 
 1   pm10              float64
 2   pm2_5             float64
 3   carbon_monoxide   float64
 4   nitrogen_dioxide  float64
 5   sulphur_dioxide   float64
 6   ozone             float64
 7   dust              float64
 8   archivo_origen    object 
 9   ciudad_id         object 
 10  anio              object 
dtypes: float64(7), object(4)
memory usage: 171.5+ MB


In [8]:
columnas_a_promediar = [
    "pm10", "pm2_5", "carbon_monoxide", "nitrogen_dioxide",
    "sulphur_dioxide", "ozone", "dust"
]

# Asegurar que anio y ciudad_id sean tipo string (puede ayudar si hay mezcla de tipos)
df_unido["anio"] = df_unido["anio"].astype(str)
df_unido["ciudad_id"] = df_unido["ciudad_id"].astype(str)

# Agrupar por ciudad y año, y calcular promedio
df_promedios = df_unido.groupby(["anio", "ciudad_id"])[columnas_a_promediar].mean().reset_index()

# Ver el resultado
df_promedios.head()


anio   ciudad_id       pm10     pm2_5  carbon_monoxide  nitrogen_dioxide  \
0  2024  1032000005   7.069490  5.085235       136.964139          3.640130   
1  2024  1032000014  10.507081  7.136270       204.553734         12.415289   
2  2024  1032000017   7.615084  5.402971       147.021175          0.717509   
3  2024  1032005345   7.582104  5.372951       142.479622          3.243431   
4  2024  1032008603   4.011851  2.689367        95.562045          1.227106   

   sulphur_dioxide      ozone      dust  
0         1.141006  49.216302  0.135701  
1         6.621755  46.321494  0.138434  
2         0.365574  55.561817  0.179076  
3         0.866359  52.460838  0.116689  
4         0.462682  47.438411  0.224613

In [9]:
columnas_contaminantes = [
    "pm10", "pm2_5", "carbon_monoxide", "nitrogen_dioxide",
    "sulphur_dioxide", "ozone", "dust"
]

df_promedios_sin_nulos = df_promedios.dropna(subset=columnas_contaminantes, how='all')

df_promedios_sin_nulos.head()

anio   ciudad_id       pm10     pm2_5  carbon_monoxide  nitrogen_dioxide  \
0  2024  1032000005   7.069490  5.085235       136.964139          3.640130   
1  2024  1032000014  10.507081  7.136270       204.553734         12.415289   
2  2024  1032000017   7.615084  5.402971       147.021175          0.717509   
3  2024  1032005345   7.582104  5.372951       142.479622          3.243431   
4  2024  1032008603   4.011851  2.689367        95.562045          1.227106   

   sulphur_dioxide      ozone      dust  
0         1.141006  49.216302  0.135701  
1         6.621755  46.321494  0.138434  
2         0.365574  55.561817  0.179076  
3         0.866359  52.460838  0.116689  
4         0.462682  47.438411  0.224613

In [10]:
df_promedios_sin_nulos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5117 entries, 0 to 5116
Data columns (total 9 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   anio              5117 non-null   object 
 1   ciudad_id         5117 non-null   object 
 2   pm10              5117 non-null   float64
 3   pm2_5             5117 non-null   float64
 4   carbon_monoxide   5117 non-null   float64
 5   nitrogen_dioxide  5117 non-null   float64
 6   sulphur_dioxide   5117 non-null   float64
 7   ozone             5117 non-null   float64
 8   dust              5117 non-null   float64
dtypes: float64(7), object(2)
memory usage: 359.9+ KB


In [11]:
conteo_por_anio_df = df_promedios_sin_nulos.groupby("anio").size().reset_index(name="cantidad_registros")
print(conteo_por_anio_df)


   anio  cantidad_registros
0  2024                5117


## Clima

In [12]:
# Ruta de la carpeta donde están los archivos
carpeta_clima = r"C:\Users\glova\OneDrive\Documentos\Clima\resultados_clima"

# Listar solo archivos de 2024 que terminen en _2024_clima.csv
archivos_2024 = [
    archivo for archivo in os.listdir(carpeta_clima)
    if archivo.endswith("_2024_clima.csv")
]

# Lista para guardar los DataFrames
dfs = []

# Leer cada archivo y agregar columna con ID
for archivo in archivos_2024:
    ruta = os.path.join(carpeta_clima, archivo)
    try:
        df = pd.read_csv(ruta, encoding='utf-8-sig')
        match = re.match(r"(\d+)_2024_clima\.csv", archivo)
        ciudad_id = match.group(1) if match else None
        df['ciudad_id'] = ciudad_id
        dfs.append(df)
    except Exception as e:
        print(f"❌ Error al leer {archivo}: {e}")

# Unir todos los archivos
df_consolidado_clima = pd.concat(dfs, ignore_index=True)

# Guardar el archivo final consolidado
archivo_salida = os.path.join(carpeta_clima, "clima_2024_completo.csv")
df_consolidado_clima.to_csv(archivo_salida, index=False, encoding="utf-8-sig")

print(f"✅ Consolidado guardado en: {archivo_salida}")


✅ Consolidado guardado en: C:\Users\glova\OneDrive\Documentos\Clima\resultados_clima\clima_2024_completo.csv


In [13]:
df_consolidado_clima.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1873188 entries, 0 to 1873187
Data columns (total 4 columns):
 #   Column                     Dtype  
---  ------                     -----  
 0   time                       object 
 1   temperature_2m_mean        float64
 2   relative_humidity_2m_mean  int64  
 3   ciudad_id                  object 
dtypes: float64(1), int64(1), object(2)
memory usage: 57.2+ MB


In [16]:
columnas_a_promediar = [
    "temperature_2m_mean", "relative_humidity_2m_mean"
]

# Asegurar que anio y ciudad_id sean tipo string (puede ayudar si hay mezcla de tipos)
df_consolidado_clima["ciudad_id"] = df_consolidado_clima["ciudad_id"].astype(str)

# Agrupar por ciudad y año, y calcular promedio
df_promedios_clima = df_consolidado_clima.groupby(["ciudad_id"])[columnas_a_promediar].mean().reset_index()

# Ver el resultado
df_promedios_clima.head()

ciudad_id  temperature_2m_mean  relative_humidity_2m_mean
0  1032000005            18.123224                  68.953552
1  1032000014            17.373497                  73.254098
2  1032000017            21.865847                  56.734973
3  1032005345            19.384153                  70.997268
4  1032008603            14.719399                  61.849727

In [17]:
columnas_clima = [
    "temperature_2m_mean", "relative_humidity_2m_mean"
]

df_promedios_sin_nulos_clima = df_promedios_clima.dropna(subset=columnas_clima, how='all')

df_promedios_sin_nulos_clima.head()

ciudad_id  temperature_2m_mean  relative_humidity_2m_mean
0  1032000005            18.123224                  68.953552
1  1032000014            17.373497                  73.254098
2  1032000017            21.865847                  56.734973
3  1032005345            19.384153                  70.997268
4  1032008603            14.719399                  61.849727

In [18]:
df_promedios_sin_nulos_clima.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5118 entries, 0 to 5117
Data columns (total 3 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   ciudad_id                  5118 non-null   object 
 1   temperature_2m_mean        5118 non-null   float64
 2   relative_humidity_2m_mean  5118 non-null   float64
dtypes: float64(2), object(1)
memory usage: 120.1+ KB


# Consolidar DF Final

In [19]:
# Asegurarse de que ambas columnas estén en tipo string (por seguridad)
df_promedios_sin_nulos_clima["ciudad_id"] = df_promedios_sin_nulos_clima["ciudad_id"].astype(str)
df_promedios_sin_nulos["ciudad_id"] = df_promedios_sin_nulos["ciudad_id"].astype(str)

# Hacer merge por ciudad_id
df_final = pd.merge(
    df_promedios_sin_nulos,               # calidad del aire
    df_promedios_sin_nulos_clima,         # clima
    on="ciudad_id",
    how="inner"                           # solo las que coincidan en ambas
)

In [20]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5117 entries, 0 to 5116
Data columns (total 11 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   anio                       5117 non-null   object 
 1   ciudad_id                  5117 non-null   object 
 2   pm10                       5117 non-null   float64
 3   pm2_5                      5117 non-null   float64
 4   carbon_monoxide            5117 non-null   float64
 5   nitrogen_dioxide           5117 non-null   float64
 6   sulphur_dioxide            5117 non-null   float64
 7   ozone                      5117 non-null   float64
 8   dust                       5117 non-null   float64
 9   temperature_2m_mean        5117 non-null   float64
 10  relative_humidity_2m_mean  5117 non-null   float64
dtypes: float64(9), object(2)
memory usage: 439.9+ KB


In [ ]:
# Ruta donde quieres guardar el archivo
ruta_salida = r"C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\clima\aire_clima_2024.csv"

# Guardar como CSV con codificación UTF-8 (excel-friendly)
df_final.to_csv(ruta_salida, index=False, encoding="utf-8-sig")

print(f"✅ Archivo guardado en: {ruta_salida}")

✅ Archivo guardado en: C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\clima\aire_clima_2024_test.csv


In [22]:
df_sudamerica = pd.read_excel(r"C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\data_sources\all_sudamerica.xlsx")
df_sudamerica.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5135 entries, 0 to 5134
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   city         5135 non-null   object 
 1   city_ascii   5135 non-null   object 
 2   lat          5135 non-null   float64
 3   lng          5135 non-null   float64
 4   country      5135 non-null   object 
 5   iso2         5135 non-null   object 
 6   iso3         5135 non-null   object 
 7   admin_name   5135 non-null   object 
 8   capital      4301 non-null   object 
 9   population   5130 non-null   float64
 10  id           5135 non-null   int64  
 11  Unnamed: 11  5135 non-null   object 
dtypes: float64(3), int64(1), object(8)
memory usage: 481.5+ KB


In [23]:
# Asegurarse de que ambas columnas sean del mismo tipo
df_final["ciudad_id"] = df_final["ciudad_id"].astype(str)
df_sudamerica["id"] = df_sudamerica["id"].astype(str)

# Merge por ID de ciudad
df_completo = pd.merge(
    df_final,
    df_sudamerica,
    left_on="ciudad_id",
    right_on="id",
    how="inner"  # o 'inner' si solo querés los que coincidan
)

In [25]:
# Asegurar que ciudad_id sea string (según tu DataFrame)
df_completo["ciudad_id"] = df_completo["ciudad_id"].astype(str)

# Filtrar los registros que NO sean esos dos ID
ids_a_excluir = ["1862763389", "1170149115"]
df_completo = df_completo[~df_completo["ciudad_id"].isin(ids_a_excluir)]

print(f"✅ Registros después del filtro: {len(df_completo)}")


✅ Registros después del filtro: 5115


In [ ]:
# Ruta donde quieres guardar el archivo
ruta_salida = r"C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\clima\aire_clima_2024_final.csv"

# Guardar como CSV con codificación UTF-8 (excel-friendly)
df_completo.to_csv(ruta_salida, index=False, encoding="utf-8-sig")

print(f"✅ Archivo guardado en: {ruta_salida}")

# FIN DE LA CONSOLIDACIÓN

✅ Archivo guardado en: C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\clima\aire_clima_2024_final.csv


# EDA

In [ ]:
# Para poder leer el resultado y poder trabajar sin estar ejecutando lasceldas previas
ruta = r"C:\Users\glova\OneDrive\Documentos\nuevo_ciudades\clima\aire_clima_2024_final.csv"
df_completo = pd.read_csv(ruta, encoding='utf-8-sig')  # 'utf-8-sig' si el archivo fue generado para compatibilidad con Excel

# Verificar primeras filas
df_completo.head()

anio   ciudad_id       PM10     PM2.5  Monóxido de carbono  \
0  2024  1032000005   7.069490  5.085235           136.964139   
1  2024  1032000014  10.507081  7.136270           204.553734   
2  2024  1032000017   7.615084  5.402971           147.021175   
3  2024  1032005345   7.582104  5.372951           142.479622   
4  2024  1032008603   4.011851  2.689367            95.562045   

   Dióxido de nitrógeno  Dióxido de azufre      Ozono     Polvo  Temperatura  \
0              3.640130           1.141006  49.216302  0.135701    18.123224   
1             12.415289           6.621755  46.321494  0.138434    17.373497   
2              0.717509           0.365574  55.561817  0.179076    21.865847   
3              3.243431           0.866359  52.460838  0.116689    19.384153   
4              1.227106           0.462682  47.438411  0.224613    14.719399   

   Humedad relativa       city city_ascii      lat      lng    country iso2  
0         68.953552    Casilda    Casilda -33.0500 -61.1667  Argentina   AR  
1         73.254098   Martínez   Martinez -34.4833 -58.5000  Argentina   AR  
2         56.734973     Recreo     Recreo -29.2667 -65.0667  Argentina   AR  
3         70.997268    Coronda    Coronda -31.9667 -60.9167  Argentina   AR  
4         61.849727  Tornquist  Tornquist -38.1000 -62.2167  Argentina   AR

In [ ]:
# Diccionario de nombres en español
nombres_es = {
    "pm10": "PM10",
    "pm2_5": "PM2.5",
    "carbon_monoxide": "Monóxido de carbono",
    "nitrogen_dioxide": "Dióxido de nitrógeno",
    "sulphur_dioxide": "Dióxido de azufre",
    "ozone": "Ozono",
    "dust": "Polvo",
    "temperature_2m_mean": "Temperatura",
    "relative_humidity_2m_mean": "Humedad relativa"
}

# Renombrar columnas en el DataFrame (por ejemplo, df_completo)
df_completo = df_completo.rename(columns=nombres_es)

In [ ]:
import plotly.express as px
import plotly.colors as pc

# Paleta con colores intensos
colores_intensos = pc.qualitative.Dark24 + pc.qualitative.Bold + pc.qualitative.Plotly

fig = px.scatter_geo(
    df_completo,
    lat='lat',
    lon='lng',
    hover_name='city',
    color='country',
    projection='natural earth',
    title="Ubicación de ciudades por país",
    color_discrete_sequence=colores_intensos
)

# Limitar la vista a Sudamérica
fig.update_geos(
    lataxis_range=[-60, 15],   # Latitudes aproximadas de Sudamérica
    lonaxis_range=[-90, -30],  # Longitudes aproximadas de Sudamérica
    visible=True
)

fig.update_layout(height=700, title_x=0.5)
fig.show()


In [ ]:
parametros = [
    "PM10", "PM2.5", "Monóxido de carbono", "Dióxido de nitrógeno", "Dióxido de azufre", "Ozono", "Polvo", "Temperatura", "Humedad relativa"
]

# Mostrar resumen estadístico solo de esas columnas
df_completo[parametros].describe()

PM10        PM2.5  Monóxido de carbono  Dióxido de nitrógeno  \
count  5115.000000  5115.000000          5115.000000           5115.000000   
mean     11.958937     8.225970           190.848426              3.795625   
std       5.971497     3.893001            80.354668              4.520111   
min       1.605578     1.108288            73.397086              0.087864   
25%       8.209614     5.570213           134.940460              1.324624   
50%      10.860189     7.541655           180.144695              2.488559   
75%      13.997769     9.701742           220.630009              4.253973   
max     111.316496    47.627778           863.911430             42.629451   

       Dióxido de azufre        Ozono        Polvo  Temperatura  \
count        5115.000000  5115.000000  5115.000000  5115.000000   
mean            1.559310    50.965649     0.588506    22.331118   
std             2.782862    10.822948     7.341496     4.607688   
min             0.015858    13.804189     0.000000     1.145628   
25%             0.385582    45.331170     0.010587    19.644126   
50%             0.700808    50.265824     0.050774    23.365847   
75%             1.475285    56.034324     0.167919    25.950273   
max            32.370196   107.849727   295.472791    29.511475   

       Humedad relativa  
count       5115.000000  
mean          73.334681  
std            8.846280  
min           16.887978  
25%           67.400273  
50%           74.527322  
75%           80.098361  
max           95.092896

In [ ]:
import plotly.express as px

# Contar cantidad de registros por país
conteo_paises = df_completo['country'].value_counts().reset_index()
conteo_paises.columns = ['country', 'cantidad']

# Crear gráfico de barras
fig = px.bar(
    conteo_paises,
    x='country',
    y='cantidad',
    title='Cantidad de registros por país',
    labels={'country': 'País', 'cantidad': 'Número de registros'},
    text='cantidad',
)

# Ajustes de estilo
fig.update_layout(
    xaxis_tickangle=-45,
    title_x=0.5  # Centrar el título
)

fig.show()


In [ ]:
import plotly.graph_objects as go

# Columnas que querés incluir (en español)
parametros = [
    "PM10", "PM2.5", "Monóxido de carbono", "Dióxido de nitrógeno",
    "Dióxido de azufre", "Ozono", "Polvo",
    "Temperatura", "Humedad relativa"
]

# Asegurarse de que las columnas estén en el DataFrame
parametros_validos = [col for col in parametros if col in df_completo.columns]

# Calcular la matriz de correlación
corr = df_completo[parametros_validos].corr()

# Crear Heatmap
fig = go.Figure(data=go.Heatmap(
    z=corr.values,
    x=corr.columns,
    y=corr.columns,
    colorscale='RdBu',
    zmin=-1,
    zmax=1,
    colorbar=dict(
        title="Coef. de Correlación",
        tickvals=[-1, -0.5, 0, 0.5, 1],
        ticktext=['-1', '-0.5', '0', '0.5', '1'],
        len=0.75
    )
))

# Añadir anotaciones con los valores
for i in range(len(corr)):
    for j in range(len(corr.columns)):
        fig.add_annotation(
            x=corr.columns[j],
            y=corr.columns[i],
            text=str(round(corr.values[i][j], 2)),
            showarrow=False,
            font=dict(color="black", size=12)
        )

fig.update_layout(
    title="Matriz de Correlación entre Variables",
    xaxis_title="Variables",
    yaxis_title="Variables",
    xaxis_showgrid=False,
    yaxis_showgrid=False,
    title_x=0.5,
    width=900,
    height=700
)

fig.show()


## Distribución de parámetros por País

In [ ]:
import plotly.express as px

parametros = [
    "PM10", "PM2.5", "Monóxido de carbono", "Dióxido de nitrógeno",
    "Dióxido de azufre", "Ozono", "Polvo",
    "Temperatura", "Humedad relativa"
]

# Crear un boxplot para cada parámetro
for parametro in parametros:
    fig = px.box(
        df_completo,
        x="country",
        y=parametro,
        color="country",
        title=f"Distribución de {parametro} por país",
        points="outliers",  # muestra los valores atípicos
    )
    fig.update_layout(
        xaxis_title="País",
        yaxis_title=parametro,
        title_x=0.5,
        showlegend=False
    )
    fig.show()


In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Lista de parámetros
parametros = [
    "PM10", "PM2.5", "Monóxido de carbono", "Dióxido de nitrógeno",
    "Dióxido de azufre", "Ozono", "Polvo",
    "Temperatura", "Humedad relativa"
]

# Crear subgrilla 5 columnas x 2 filas
fig = make_subplots(
    rows=5, cols=2,
    subplot_titles=parametros,
    horizontal_spacing=0.06,
    vertical_spacing=0.06
)

# Añadir cada boxplot en la posición correspondiente
for i, parametro in enumerate(parametros):
    row = i // 2 + 1  # fila 1 o 2
    col = i % 2 + 1   # columna 1 a 5
    for pais in df_completo['country'].unique():
        fig.add_trace(
            go.Box(
                y=df_completo[df_completo['country'] == pais][parametro],
                name=pais,
                boxpoints="outliers",
                marker=dict(size=2),
                line=dict(width=1),
                showlegend=False
            ),
            row=row, col=col
        )

# Ajustes del diseño
fig.update_layout(
    height=1500,
    title_text="Boxplots de variables ambientales por país",
    title_x=0.5
)

fig.show()


## Distribución por Parámetro

In [ ]:
import plotly.express as px
import plotly.colors as pc

# Filtrar solo columnas float, excluyendo lat y lng explícitamente
float_cols = df_completo.select_dtypes(include='float64').columns
float_cols = [col for col in float_cols if col not in ["lat", "lng", "population"]]

# Paleta de colores
colores = pc.qualitative.Plotly

# Dibujar histogramas
for i, col in enumerate(float_cols):
    color = colores[i % len(colores)]
    fig = px.histogram(
        df_completo,
        x=col,
        nbins=50,
        title=f"Histograma de {col}",
        color_discrete_sequence=[color]
    )
    fig.show()


In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.colors as pc

# Filtrar columnas numéricas deseadas
float_cols = df_completo.select_dtypes(include='float64').columns
float_cols = [col for col in float_cols if col not in ["lat", "lng", "population"]]

# Limitar a 9 columnas (o elegí las que quieras)
cols_a_graficar = float_cols[:9]

# Paleta de colores fuerte
colores = pc.qualitative.Plotly

# Crear figura 3x3
fig = make_subplots(rows=3, cols=3, subplot_titles=cols_a_graficar)

# Agregar un histograma por cada subplot
for i, col in enumerate(cols_a_graficar):
    fila = i // 3 + 1
    columna = i % 3 + 1
    color = colores[i % len(colores)]

    fig.add_trace(
        go.Histogram(
            x=df_completo[col],
            nbinsx=50,
            marker_color=color,
            name=col,
            showlegend=False
        ),
        row=fila, col=columna
    )

# Configurar layout general
fig.update_layout(
    height=900,
    width=1000,
    title_x=0.5,
    title_text="Histogramas de variables de calidad del aire y climáticas",
    showlegend=False
)

fig.show()


## Visualización de parámetro atípico: Polvo

In [ ]:
import plotly.express as px

# Escala:
# 0 → verde (#448D47)
# 5 → amarillo (#fff700)
# 10 → amarillo más claro (#ffffcc)
# >10 → rojo (#d11212)
# >120 → negro (#000000)

escala_personalizada = [
    (0.00, "#448D47"),     # verde oscuro (0)
    (0.041, "#fff700"),    # amarillo (~5)
    (0.083, "#ffffcc"),    # amarillo muy claro (~10)
    (0.084, "#d11212"),    # rojo desde >10
    (1.00, "#000000")      # negro desde 120+
]

fig = px.scatter_geo(
    df_completo,
    lat='lat',
    lon='lng',
    hover_name='city',
    color='Polvo',
    projection='natural earth',
    title="Concentración de polvo atmosférico en ciudades de Sudamérica",
    color_continuous_scale=escala_personalizada,
    range_color=(0, 120)
)

fig.update_geos(
    lataxis_range=[-60, 15],
    lonaxis_range=[-90, -30],
    visible=True
)

fig.update_layout(
    height=700,
    title_x=0.5,
    coloraxis_colorbar=dict(
        title="Polvo (µg/m³)",
        tickvals=[0, 5, 10, 60, 120],
        ticktext=["0", "5", "10", "60", "120+"],
        len=0.75,
        thickness=15
    )
)

fig.show()
